In [1]:
#@title いつのテスト結果かと，入力ファイル名を指定

# いつの（どのフォルダの）テスト結果かを指定
date = "GEF01-27[18:10]" #@param {type:"string"}

# 入力ファイル名を指定（拡張子なし）
input_file_name = 'test_gef_results' #@param {type:"string"}


In [2]:
#@title ファイルパス設定
input_file = f'/content/drive/MyDrive/B4kiya/results/{date}/test/gef/{input_file_name}.csv'
output_file = f'/content/drive/MyDrive/B4kiya/results/{date}/test/gef/evaluation_{input_file_name}.csv'

In [3]:
#@title Google Driveをマウントする
from google.colab import drive
drive.mount('/content/drive/')

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [4]:
#@title 必要なライブラリをインストールする
!pip install deepeval==2.2.6  # deepeval: LLMの評価のためのライブラリ
!pip install ngrok  # ngrok: ローカルサーバーを外部に公開するためのツール
!pip install pyngrok # pyngrok: ngrokをPythonから操作するためのライブラリ

In [5]:
# Ollamaをインストールする
!curl https://ollama.ai/install.sh | sh

# CUDAドライバーをインストールする
!echo 'debconf debconf/frontend select Noninteractive' | sudo debconf-set-selections
!sudo apt-get update && sudo apt-get install -y cuda-drivers

# 環境変数を設定する
import os
os.environ.update({'LD_LIBRARY_PATH': '/usr/lib64-nvidia'})

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 13269    0 13269    0     0  53470      0 --:--:-- --:--:-- --:--:-- 53504
>>> Cleaning up old version at /usr/local/lib/ollama
>>> Installing ollama to /usr/local
>>> Downloading Linux amd64 bundle
############################################################################################# 100.0%
>>> Creating ollama user...
>>> Adding ollama user to video group...
>>> Adding current user to ollama group...
>>> Creating ollama systemd service...
>>> The Ollama API is now available at 127.0.0.1:11434.
>>> Install complete. Run "ollama" from the command line.
Get:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,626 B]
Get:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease [1,581 B]
Get:3 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Hit:4 http:/

In [6]:
#@title Ollamaサーバーをバックグラウンドで起動する
!nohup ollama serve &

nohup: appending output to 'nohup.out'


In [7]:
#@title セッション終了時に，ollamaサーバを終了
import atexit
import os

def stop_ollama_server():
  os.system("pkill ollama")

atexit.register(stop_ollama_server)

<function __main__.stop_ollama_server()>

In [8]:
#@title llama3.2モデルをダウンロードする
# サーバーの起動を待つ
import time
time.sleep(10)

# llama3.2モデルをダウンロードする
!ollama pull llama3.2

pulling manifest ⠋ pulling manifest ⠙ pulling manifest ⠹ pulling manifest ⠸ pulling manifest ⠼ pulling manifest ⠴ pulling manifest 
pulling dde5aa3fc5ff...   0% ▕▏    0 B/2.0 GB                  pulling manifest 
pulling dde5aa3fc5ff...   0% ▕▏    0 B/2.0 GB                  pulling manifest 
pulling dde5aa3fc5ff...   0% ▕▏ 569 KB/2.0 GB                  pulling manifest 
pulling dde5aa3fc5ff...   1% ▕▏  20 MB/2.0 GB                  pulling manifest 
pulling dde5aa3fc5ff...   4% ▕▏  81 MB/2.0 GB                  pulling manifest 
pulling dde5aa3fc5ff...   7% ▕▏ 135 MB/2.0 GB                  pulling manifest 
pulling dde5aa3fc5ff...   7% ▕▏ 145 MB/2.0 GB                  pulling manifest 
pulling dde5aa3fc5ff...   8% ▕▏ 169 MB/2.0 GB                  pulling manifest 
pulling dde5aa3fc5ff...  10% ▕▏ 208 MB/2.0 GB                  pulling manifest 
pulling dde5aa3fc5ff...  11% ▕▏ 224 MB/2.0 GB                  pulling manifest 
pulling dde5aa3fc5ff...  12% ▕▏ 250 MB/2.0 GB  250 MB/s   

In [9]:
#@title Ollamaをインストールする
!pip install ollama

In [10]:
#@title deepevalにローカルモデルを設定する
import ollama
!deepeval set-local-model --model-name=llama3.2 \
    --base-url="http://localhost:11434/v1/" \
    --api-key="ollama"

/usr/local/lib/python3.11/dist-packages/deepeval/__init__.py:52: UserWarning: You are using deepeval version 2.2.6, however version 2.2.9 is available. You should consider upgrading via the "pip install --upgrade deepeval" command.
  warnings.warn(
🙌 Congratulations! You're now using a local model for all evals that require an LLM.


In [11]:
#@title タイムアウト時間を設定
import signal

class TimeoutException(Exception):
    pass

def timeout_handler(signum, frame):
    raise TimeoutException("60秒タイムアウトしました")

# タイムアウト時間を設定 (秒)
timeout_duration = 60

In [12]:
#@title 評価メトリックを定義する
from deepeval.metrics import GEval # deepevalからGEvalメトリックをインポートします．GEvalは，生成されたテキストの正確性を評価するためのメトリックです．
from deepeval.test_case import LLMTestCaseParams # deepevalからLLMTestCaseParamsをインポートします．LLMTestCaseParamsは，テストケースのパラメータを定義するためのクラスです．

similarity_metric = GEval(
    name="Semantic Similarity",
    criteria="Determine the semantic similarity between the actual output and the expected output. "
             "If the similarity score is 0.7 or higher, the output is acceptable. Otherwise, it is considered inadequate.",
    evaluation_params=[LLMTestCaseParams.ACTUAL_OUTPUT, LLMTestCaseParams.EXPECTED_OUTPUT],
    model="llama3.2",
    threshold=0.7   # 0.7 を基準点として適用
)

grammar_metric = GEval(
    name="Grammar Accuracy",
    criteria="Evaluate the grammatical correctness of the actual output. "
             "If the score is 0.7 or higher, the grammar is acceptable. "
             "If the score is below 0.7, the output is considered grammatically incorrect.",
    evaluation_params=[LLMTestCaseParams.ACTUAL_OUTPUT],
    model="llama3.2",
    threshold=0.7
)

fluency_metric = GEval(
    name="Fluency & Readability",
    criteria="Evaluate the fluency and readability of the actual output. "
             "A score of 0.7 or higher indicates good readability. "
             "If the score is below 0.7, the text is considered difficult to read.",
    evaluation_params=[LLMTestCaseParams.ACTUAL_OUTPUT],
    model="llama3.2",
    threshold=0.7
)

/usr/local/lib/python3.11/dist-packages/deepeval/__init__.py:52: UserWarning: You are using deepeval version 2.2.6, however version 2.2.9 is available. You should consider upgrading via the "pip install --upgrade deepeval" command.
  warnings.warn(


In [13]:
#@title 評価を実行し、TSVに出力する
import pandas as pd
from deepeval.test_case import LLMTestCase
from tqdm.auto import tqdm

# データ読み込み
try:
    data = pd.read_csv(input_file, sep=',')
except pd.errors.ParserError as e:
    print(f"エラーが発生した行: {e.lineno}")
    # エラーが発生した行の前後数行を表示して確認
    with open(input_file, 'r') as f:
        lines = f.readlines()
        for i in range(max(0, e.lineno - 5), min(len(lines), e.lineno + 5)):
            print(f"{i+1}: {lines[i].strip()}")

# スコアと理由を保存するリストの初期化
similarity_scores, similarity_reasons = [], []
grammar_scores, grammar_reasons = [], []
fluency_scores, fluency_reasons = [], []

# 各行に対して評価を実行
for _, row in tqdm(data.iterrows(), total=data.shape[0], desc="Evaluating"):
    # =========================
    # 意味的類似度評価
    # =========================
    try:
        signal.signal(signal.SIGALRM, timeout_handler)
        signal.alarm(timeout_duration)

        similarity_test_case = LLMTestCase(
            input=row['Statement'],
            actual_output=row['Generated Justification'],
            expected_output=row['Gold Justification']
        )
        similarity_metric.measure(similarity_test_case)
        similarity_scores.append(similarity_metric.score)
        similarity_reasons.append(similarity_metric.reason)

        signal.alarm(0)
    except TimeoutException:
        print(f"行 {row.name} の意味的類似度評価でタイムアウトしました")
        similarity_scores.append(None)
        similarity_reasons.append("Timeout")
    except Exception as e:
        if "Connection" in str(e):
            raise
        else:
            print(f"行 {row.name} の意味的類似度評価でエラーが発生しました: {e}")
            similarity_scores.append(None)
            similarity_reasons.append(str(e))

    # =========================
    # 文法の正確さ評価
    # =========================
    try:
        signal.signal(signal.SIGALRM, timeout_handler)
        signal.alarm(timeout_duration)

        grammar_test_case = LLMTestCase(
            input=row['Statement'],
            actual_output=row['Generated Justification']
        )
        grammar_metric.measure(grammar_test_case)
        grammar_scores.append(grammar_metric.score)
        grammar_reasons.append(grammar_metric.reason)

        signal.alarm(0)
    except TimeoutException:
        print(f"行 {row.name} の文法の正確さ評価でタイムアウトしました")
        grammar_scores.append(None)
        grammar_reasons.append("Timeout")
    except Exception as e:
        if "Connection" in str(e):
            raise
        else:
            print(f"行 {row.name} の文法の正確さ評価でエラーが発生しました: {e}")
            grammar_scores.append(None)
            grammar_reasons.append(str(e))

    # =========================
    # 読みやすさ評価
    # =========================
    try:
        signal.signal(signal.SIGALRM, timeout_handler)
        signal.alarm(timeout_duration)

        fluency_test_case = LLMTestCase(
            input=row['Statement'],
            actual_output=row['Generated Justification']
        )
        fluency_metric.measure(fluency_test_case)
        fluency_scores.append(fluency_metric.score)
        fluency_reasons.append(fluency_metric.reason)

        signal.alarm(0)
    except TimeoutException:
        print(f"行 {row.name} の読みやすさ評価でタイムアウトしました")
        fluency_scores.append(None)
        fluency_reasons.append("Timeout")
    except Exception as e:
        if "Connection" in str(e):
            raise
        else:
            print(f"行 {row.name} の読みやすさ評価でエラーが発生しました: {e}")
            fluency_scores.append(None)
            fluency_reasons.append(str(e))

# スコアと理由をデータフレームに追加
data['Semantic Similarity Score'] = similarity_scores
data['Semantic Similarity Reason'] = similarity_reasons
data['Grammar Accuracy Score'] = grammar_scores
data['Grammar Accuracy Reason'] = grammar_reasons
data['Fluency & Readability Score'] = fluency_scores
data['Fluency & Readability Reason'] = fluency_reasons


# ファイル保存
data.to_csv(output_file, sep='\t', index=False)
print(f"Evaluation results saved to {output_file}")

Output hidden; open in https://colab.research.google.com to view.

In [14]:
#@title ランタイムの切断
from google.colab import runtime
runtime.unassign()